In [1]:
from sklearn.model_selection import KFold
import pandas as pd

In [2]:
import wandb
wandb.login()

wandb: Currently logged in as: konggedzu (imucs). Use `wandb login --relogin` to force relogin


True

In [3]:
sweep_config = {
    'method': 'random'
}

In [4]:
metric = {
    'name': 'Grand Mean',
    'goal': 'maximize'
}

sweep_config['metric'] = metric

In [5]:
parameters_dict = {
    'dropout': {
          'values': [0.1, 0.2, 0.3, 0.4, 0.5, 0.6, 0.7, 0.8, 0.9]
        },

    'learning_rate': {
        'distribution': 'uniform',
        'min': 0,
        'max': 0.1
        },

    'batch_size': {
        'values': [256, 512, 1024, 2048, 4096]
        },

    'data_augmentation_multiple': {
        'values': [1, 3, 5, 7]
        }
}

In [6]:
sweep_config['parameters'] = parameters_dict

In [7]:
sweep_id = wandb.sweep(sweep_config, project="pytorch-sweeps-sub_loc_train_no_aug")

Create sweep with ID: apgc2q24
Sweep URL: https://wandb.ai/imucs/pytorch-sweeps-sub_loc_train_no_aug/sweeps/apgc2q24


In [8]:
import pprint

pprint.pprint(sweep_config)

{'method': 'random',
 'metric': {'goal': 'maximize', 'name': 'Grand Mean'},
 'parameters': {'batch_size': {'values': [256, 512, 1024, 2048, 4096]},
                'data_augmentation_multiple': {'values': [1, 3, 5, 7]},
                'dropout': {'values': [0.1,
                                       0.2,
                                       0.3,
                                       0.4,
                                       0.5,
                                       0.6,
                                       0.7,
                                       0.8,
                                       0.9]},
                'learning_rate': {'distribution': 'uniform',
                                  'max': 0.1,
                                  'min': 0}}}


In [9]:
feature_pd = pd.read_csv('/home/kongge/projects/new_protT5/data/DPC_T5_578_right.csv')
labels_pd = pd.read_csv("/home/kongge/projects/new_protT5/data/mutil_label_578.csv")

In [10]:
from dataAug.tools import MLDA

In [11]:
from dataAug.all_tools import dataAugSMOTE

In [12]:

smote_multiple = {}

In [13]:
import time
from classify.targeTools import testThresholdFive, Accuracy
from torch import optim
from torch.utils.data import DataLoader, TensorDataset
import torch
from Classify_adjust import ModelClassify
def train_and_val(config=None):
    with wandb.init(config=config):
        config = wandb.config
        kf = KFold(n_splits=10, shuffle=True)
        model_discord = []
        for train_index, test_index in kf.split(feature_pd):
            train_true_data = feature_pd.iloc[train_index]
            train_true_label = labels_pd.iloc[train_index]


            test_data = feature_pd.iloc[test_index]
            test_label = labels_pd.iloc[test_index]

            datasetTrain = TensorDataset(torch.tensor(train_true_data.values), torch.tensor(train_true_label.values))
            batch_size = config.batch_size
            dataloaderTrain = DataLoader(datasetTrain, batch_size=batch_size, shuffle=True)

            datasetTest = TensorDataset(torch.tensor(test_data.values), torch.tensor(test_label.values))

            batch_size = len(datasetTest)
            dataloaderTest = DataLoader(datasetTest, batch_size=batch_size, shuffle=False)

            model = ModelClassify(drop_rate=config.dropout, num_class=5, feature_num=1424)
            criterion = torch.nn.BCELoss()
            optimizer = optim.Adam(model.parameters(), lr=config.learning_rate)
            import warnings
            warnings.filterwarnings("ignore")
            GMList = {}
            epochs = 200
            for epoch in range(epochs):
                model.train()
                total_loss = 0.0
                for idx, data in enumerate(dataloaderTrain, 0):
                    inputs, labels = data
                    labels = labels.float()
                    inputs = inputs.float()
                    out = model(inputs)
                    loss = criterion(out, labels)
                    optimizer.zero_grad()
                    loss.backward()
                    optimizer.step()
                    total_loss += loss.item()
                avg_loss = total_loss / len(dataloaderTrain)
                threshold = 0.5
                labels_cov = torch.where(out > threshold, torch.tensor(1), torch.tensor(0))
                print(f"Epoch [{epoch+1}/{epochs}], Average Loss: {avg_loss:.4f}, ACC: {Accuracy(labels.int(), labels_cov)}")
                GMScore1 = testThresholdFive(epoch, model, dataloaderTest, class_num=5)
                GMList[epoch] = GMScore1
            t = time.time()
            best_key = max(GMList, key=GMList.get)
            best_value = GMList[best_key]
            best_value = [x.item() if isinstance(x, torch.Tensor) else x for x in best_value]
            model_discord.append(best_value)
        model_discord_column_means = [sum(col) / len(col) for col in zip(*model_discord)]
        smote_multiple[int(t)] = model_discord_column_means
        wandb.log({"Grand Mean": model_discord_column_means[0]})

In [14]:
wandb.agent(sweep_id, train_and_val, count=20)

wandb: Agent Starting Run: 1zf3xyvi with config:
wandb: 	batch_size: 4096
wandb: 	data_augmentation_multiple: 7
wandb: 	dropout: 0.4
wandb: 	learning_rate: 0.09391048396227944


Epoch [1/200], Average Loss: 0.7322, ACC: 0.21483974358974336
epoch:0, bestThreshold:[0.01, 0.01, 0.01, 0.01, 0.01], GM:0.33160918951034546, OAA:0.08620689655172414, ACC:0.3160919540229885, F1:0.39367809891700745
Epoch [2/200], Average Loss: 1.0172, ACC: 0.19394230769230753
epoch:1, bestThreshold:[0.01, 0.01, 0.01, 0.01, 0.01], GM:0.25247126817703247, OAA:0.0, ACC:0.17643678160919538, F1:0.2770114243030548
Epoch [3/200], Average Loss: 1.3102, ACC: 0.2758012820512819
epoch:2, bestThreshold:[0.01, 0.01, 0.01, 0.01, 0.01], GM:0.4252873361110687, OAA:0.3793103448275862, ACC:0.4224137931034483, F1:0.4367815852165222
Epoch [4/200], Average Loss: 0.6463, ACC: 0.4884615384615386
epoch:3, bestThreshold:[0.3, 0.01, 0.01, 0.01, 0.65], GM:0.4333333373069763, OAA:0.39655172413793105, ACC:0.43103448275862066, F1:0.44252872467041016
Epoch [5/200], Average Loss: 0.5211, ACC: 0.4253205128205128
epoch:4, bestThreshold:[0.01, 0.01, 0.01, 0.01, 0.51], GM:0.4494253098964691, OAA:0.43103448275862066, ACC:0.

wandb: Agent Starting Run: z6ep2hvi with config:
wandb: 	batch_size: 4096
wandb: 	data_augmentation_multiple: 3
wandb: 	dropout: 0.8
wandb: 	learning_rate: 0.0873382426956731


Epoch [1/200], Average Loss: 0.7229, ACC: 0.19371794871794862
epoch:0, bestThreshold:[0.01, 0.01, 0.01, 0.01, 0.02], GM:0.3950574994087219, OAA:0.1896551724137931, ACC:0.37787356321839083, F1:0.4436781108379364
Epoch [2/200], Average Loss: 0.8501, ACC: 0.17573717948717935
epoch:1, bestThreshold:[0.01, 0.01, 0.41, 0.01, 0.01], GM:0.3047701418399811, OAA:0.15517241379310345, ACC:0.28160919540229884, F1:0.33563220500946045
Epoch [3/200], Average Loss: 0.5998, ACC: 0.23253205128205123
epoch:2, bestThreshold:[0.04, 0.01, 0.01, 0.01, 0.01], GM:0.3407471179962158, OAA:0.2413793103448276, ACC:0.3290229885057472, F1:0.36321836709976196
Epoch [4/200], Average Loss: 0.6103, ACC: 0.178525641025641
epoch:3, bestThreshold:[0.91, 0.01, 0.88, 0.01, 0.96], GM:0.363103449344635, OAA:0.2413793103448276, ACC:0.3505747126436781, F1:0.39022988080978394
Epoch [5/200], Average Loss: 0.6220, ACC: 0.2001602564102564
epoch:4, bestThreshold:[0.01, 0.01, 0.01, 0.01, 0.73], GM:0.3868390619754791, OAA:0.224137931034

wandb: Agent Starting Run: e3iac409 with config:
wandb: 	batch_size: 4096
wandb: 	data_augmentation_multiple: 7
wandb: 	dropout: 0.2
wandb: 	learning_rate: 0.0498008073757941


...

Epoch [1/200], Average Loss: 0.7348, ACC: 0.28125
epoch:0, bestThreshold:[0.01, 0.01, 0.01, 0.01, 0.01], GM:0.1970689594745636, OAA:0.0, ACC:0.13850574712643676, F1:0.21609193086624146
Epoch [2/200], Average Loss: 0.5411, ACC: 0.625
epoch:1, bestThreshold:[0.01, 0.01, 0.01, 0.01, 0.98], GM:0.4551723897457123, OAA:0.3448275862068966, ACC:0.4482758620689655, F1:0.4827585816383362
Epoch [3/200], Average Loss: 0.8318, ACC: 0.125
epoch:2, bestThreshold:[0.92, 0.01, 0.01, 0.95, 0.09], GM:0.522988498210907, OAA:0.43103448275862066, ACC:0.5172413793103449, F1:0.545976996421814
Epoch [4/200], Average Loss: 0.4899, ACC: 0.4375
epoch:3, bestThreshold:[0.02, 0.19, 0.01, 0.01, 0.96], GM:0.45057469606399536, OAA:0.41379310344827586, ACC:0.4482758620689655, F1:0.4597701132297516
Epoch [5/200], Average Loss: 0.5247, ACC: 0.4375
epoch:4, bestThreshold:[0.01, 0.02, 0.9, 0.01, 0.04], GM:0.545976996421814, OAA:0.39655172413793105, ACC:0.5316091954022988, F1:0.580459713935852
Epoch [6/200], Average Loss: 0

wandb: Agent Starting Run: 7zsjhrxo with config:
wandb: 	batch_size: 512
wandb: 	data_augmentation_multiple: 5
wandb: 	dropout: 0.2
wandb: 	learning_rate: 0.09519447861823326


Epoch [1/200], Average Loss: 0.8249, ACC: 0.4166666666666667
epoch:0, bestThreshold:[0.01, 0.01, 0.01, 0.01, 0.01], GM:0.4247126579284668, OAA:0.3448275862068966, ACC:0.4195402298850575, F1:0.44540226459503174
Epoch [2/200], Average Loss: 1.3882, ACC: 0.3375
epoch:1, bestThreshold:[0.01, 0.59, 0.66, 0.01, 0.82], GM:0.2526436746120453, OAA:0.017241379310344827, ACC:0.21408045977011497, F1:0.2977011501789093
Epoch [3/200], Average Loss: 1.5626, ACC: 0.375
epoch:2, bestThreshold:[0.12, 0.01, 0.01, 0.01, 0.01], GM:0.388505756855011, OAA:0.3103448275862069, ACC:0.38218390804597696, F1:0.4080459475517273
Epoch [4/200], Average Loss: 0.5804, ACC: 0.375
epoch:3, bestThreshold:[0.01, 0.01, 0.07, 0.01, 0.01], GM:0.3459770083427429, OAA:0.3275862068965517, ACC:0.3448275862068966, F1:0.3505747318267822
Epoch [5/200], Average Loss: 1.2972, ACC: 0.125
epoch:4, bestThreshold:[0.09, 0.31, 0.01, 0.01, 0.01], GM:0.39885056018829346, OAA:0.3620689655172414, ACC:0.39655172413793105, F1:0.4080459773540497


wandb: Sweep Agent: Waiting for job.
wandb: Job received.
wandb: Agent Starting Run: x889kafl with config:
wandb: 	batch_size: 256
wandb: 	data_augmentation_multiple: 3
wandb: 	dropout: 0.5
wandb: 	learning_rate: 0.0703066855613599


Epoch [1/200], Average Loss: 0.7923, ACC: 0.15625
epoch:0, bestThreshold:[0.01, 0.01, 0.01, 0.01, 0.01], GM:0.33988505601882935, OAA:0.06896551724137931, ACC:0.3146551724137931, F1:0.4034481942653656
Epoch [2/200], Average Loss: 0.6272, ACC: 0.3125
epoch:1, bestThreshold:[0.01, 0.89, 0.01, 0.01, 0.01], GM:0.241954043507576, OAA:0.1896551724137931, ACC:0.23850574712643677, F1:0.25574713945388794
Epoch [3/200], Average Loss: 0.5474, ACC: 0.5
epoch:2, bestThreshold:[0.01, 0.84, 0.01, 0.01, 0.01], GM:0.4051724076271057, OAA:0.3620689655172414, ACC:0.4022988505747127, F1:0.4166666567325592
Epoch [4/200], Average Loss: 0.4663, ACC: 0.5
epoch:3, bestThreshold:[0.92, 0.01, 0.01, 0.01, 0.98], GM:0.5011494159698486, OAA:0.4827586206896552, ACC:0.5, F1:0.5057471394538879
Epoch [5/200], Average Loss: 0.7881, ACC: 0.0
epoch:4, bestThreshold:[0.01, 0.01, 0.17, 0.65, 0.98], GM:0.483908087015152, OAA:0.46551724137931033, ACC:0.4827586206896552, F1:0.4885057508945465
Epoch [6/200], Average Loss: 0.6743

In [15]:
smote_multiple

{1695114596: [0.8963604629039764,
  0.8650030248033879,
  0.8943158903004637,
  0.9083030819892883,
  0.9097852408885956,
  0.904395067691803],
 1695117775: [0.8234008908271789,
  0.754355716878403,
  0.8181488203266788,
  0.8314377963542938,
  0.8726860284805298,
  0.840376102924347],
 1695120727: [0.8961040556430817,
  0.868421052631579,
  0.8943738656987297,
  0.9082123458385467,
  0.9064882099628448,
  0.9030248165130615],
 1695123710: [0.8548701405525208,
  0.8079552329098609,
  0.8520669489816495,
  0.8650786399841308,
  0.8825922548770905,
  0.8666576206684112],
 1695126610: [0.8755006968975068,
  0.8392316999395039,
  0.8733161927808025,
  0.8851028501987457,
  0.8950393319129943,
  0.8848135054111481],
 1695129821: [0.7940098822116852,
  0.7476104053236541,
  0.7907844323452309,
  0.8026315808296204,
  0.8232708215713501,
  0.8057522058486939],
 1695134036: [0.4943105399608612,
  0.2525408348457351,
  0.4696284533172011,
  0.4743975728750229,
  0.7259528160095214,
  0.54903299

In [16]:
import json
file = open("/home/kongge/projects/new_protT5/data/dictionary_data_no_aug.json", "w")
json.dump(smote_multiple, file)
file.close()